In [1]:
# How many homes in Berkeley cannot be built today?
# First, generate the parcels and the zoning
import pandas as pd
import geopandas as gpd

In [2]:
zoning = gpd.read_file("/Users/darrellowens/Documents/Census Housing Stats/berkeley_zoning/berkeley_zoning.shp").to_crs("EPSG:2227")
parcels = gpd.read_file("/Users/darrellowens/Documents/Census Housing Stats/berkeley_parcels/berkeley_parcels.shp").to_crs("EPSG:2227")
# Exclude manually identified outliers in Unit Counts
outliers = [20039, 17900, 10330, 6863, 4837]
print(len(parcels))
parcels = parcels[~parcels['OBJECTID'].isin(outliers)]
print(len(parcels))

/opt/anaconda3/lib/python3.12/site-packages/pyogrio/raw.py:198: UserWarning: Measured (M) geometry types are not supported. Original type 'Measured 3D Polygon' is converted to 'Polygon Z'
  return ogr_read(


29139
29134


In [3]:
zoning['ZONECLASS'].unique()

array(['C-AC', 'C-C', 'C-DMU Buffer', 'C-DMU Core', 'C-DMU Corridor',
       'C-DMU Outer Core', 'C-E', 'C-N', 'C-N(H)', 'C-NS', 'C-NS(H)',
       'C-SA', 'C-SO', 'C-T', 'C-U', 'C-W', 'ES-R', 'MM', 'MULI', 'MUR',
       'R-1', 'R-1A', 'R-1H', 'R-2', 'R-2A', 'R-2AH', 'R-2H', 'R-3',
       'R-3H', 'R-4', 'R-4H', 'R-5', 'R-5H', 'R-BMU', 'R-S', 'R-SH',
       'R-SMU', 'SP', 'U', 'X', 'MRD', 'M'], dtype=object)

In [4]:
parcels.head()

OBJECTID Condo  Shape.STAr  Shape.STLe       PARCELID           APN  \
0       1.0  None  150.754292   61.809205  016 141000101   16-1410-1-1   
1       2.0  None   64.995179   39.052227  016 141001801  16-1410-18-1   
2       3.0  None   92.848370   67.134795  016 141002201  16-1410-22-1   
3       4.0  None   46.309411   36.530987  016 141003200    16-1410-32   
4       5.0  None  130.829117   64.288117  016 141404300    16-1414-43   

  DATE_UPDAT    SitusStree SitusStr_1 SitusUnit  ... EconomicUn  \
0       None  BENVENUE AVE       3101      None  ...        1.0   
1       None  BENVENUE AVE       6414      None  ...        1.0   
2       None  ALCATRAZ AVE       2607      None  ...        1.0   
3       None  BENVENUE AVE       6420      None  ...        0.0   
4       None    WOOLSEY ST       2400      None  ...        1.0   

                         SitusAddre                               MailingA_5  \
0  3101 BENVENUE AVE BERKELEY 94705  1255 25TH ST NW 620 WASHINGTON DC 20037   
1  6414 BENVENUE AVE BERKELEY 94618             388 61ST ST OAKLAND CA 94618   
2  2607 ALCATRAZ AVE BERKELEY 94705           1335 GROVE ST ALAMEDA CA 94501   
3  6420 BENVENUE AVE BERKELEY 94618       6428 BENVENUE AVE OAKLAND CA 94618   
4    2400 WOOLSEY ST BERKELEY 94705        2400 WOOLSEY ST BERKELEY CA 94705   

        APN_SORT  BLDSQFTTAX    LONG_DEG    LAT_DEG               LastEdited  \
0  016 141000101      1055.0 -122.253714  37.853670  2010/08/04 17:00:00.000   
1  016 141001801         0.0 -122.253029  37.851627  2020/11/30 16:00:00.000   
2  016 141002201       837.0 -122.253011  37.851406  2021/07/07 17:00:00.000   
3  016 141003200         0.0 -122.253050  37.851762  1996/05/16 17:00:00.000   
4  016 141404300      1000.0 -122.258074  37.853098  2022/11/17 16:00:00.000   

    EditType                                           geometry  
0  Unchanged  POLYGON ((6055414.223 2138042.284, 6055333.604...  
1  Unchanged  POLYGON ((6055562.389 2137305.167, 6055562.747...  
2  Unchanged  POLYGON ((6055571.467 2137175.708, 6055557.618...  
3  Unchanged  POLYGON ((6055559.367 2137325.554, 6055547.497...  
4  Unchanged  POLYGON ((6054155.538 2137860.21, 6054066.714 ...  

[5 rows x 52 columns]

In [5]:
parcels['OBJECTID'].duplicated().any()

False

In [6]:
# Merge zoning and parcels
parcels['centroid'] = parcels.geometry.centroid
parcels = parcels.set_geometry('centroid')
parcels_with_zones = gpd.sjoin(parcels, zoning[['ZONECLASS', 'geometry']], how='left', predicate='intersects')
parcels_with_zones.set_geometry('geometry', inplace=True)
parcels_with_zones.drop(columns=['centroid'], inplace=True)
parcels = gpd.GeoDataFrame(parcels_with_zones, geometry='geometry',crs=parcels_with_zones.crs)

In [7]:
print(parcels.crs)
parcels['lot_size_sqft'] = parcels['geometry'].area
parcels['lot_size_sqft'] = parcels['lot_size_sqft'].astype(int)
parcels[['LotSize', 'lot_size_sqft']].head()
#parcels['lot_size_sqft'] = parcels.geometry.area

EPSG:2227


LotSize  lot_size_sqft
0   1639.0           1623
1    200.0            699
2   1000.0            999
3    499.0            498
4   1412.0           1409

In [ ]:
import numpy as np
parcels['legality'] = 1
# How many multi-family properties are in single-family zones
parcels['legality'] = np.where(parcels['ZONECLASS'].isin(['R-1', 'R-1H']) & (parcels['Units'] > 1), 0, parcels['legality'])

# R-1A : R-1 unless lot exceeds 4,500 SQFT
mask_r1a = parcels['ZONECLASS'] == 'R-1A'
illegal_small_lot = mask_r1a & (parcels['LotSize'] < 4500) & (parcels['Units'] > 1)
illegal_large_lot = mask_r1a & (parcels['LotSize'] >= 4500) & (parcels['Units'] > 2)
parcels['legality'] = np.where(illegal_small_lot | illegal_large_lot, 0, parcels['legality'])

# R-2 1 dwelling per 2,500 square feet with one extra if remainder lot size is between 2000 and 2500
zone_mask = parcels['ZONECLASS'].isin(['R-2', 'R-2H'])
base_units = parcels['LotSize'] // 2500
bonus_unit = (parcels['LotSize'] % 2500) >= 2000
max_units = base_units + bonus_unit.astype(int)
unit_exceeds = parcels['Units'] > max_units

parcels['legality'] = np.where(
    zone_mask & (parcels['Units'] > 1) & unit_exceeds,
    0,
    parcels['legality']
)
# R-2A dwelling per 1650 with one extra if remainder lot size is between 1300 and 1650
zone_mask = parcels['ZONECLASS'].isin(['R-2A', 'R-2AH'])
unit_exceeds = parcels['Units'] > (parcels['LotSize'] // 1650)

base_units = parcels['LotSize'] // 1650
bonus_unit = (parcels['LotSize'] % 1650) >= 1300
max_units = base_units + bonus_unit.astype(int)
unit_exceeds = parcels['Units'] > max_units 

parcels['legality'] = np.where(
    zone_mask & (parcels['Units'] > 1) & unit_exceeds,
    0,
    parcels['legality']
)


In [9]:
# Exclude parcels w/o homes on them
middle_housing_housings = parcels[parcels['ZONECLASS'].isin(['R-1', 'R-2', 'R-1A', 'R-2A']) & (parcels['Units'] > 0)]
middle_housing_housings_with_hillside = parcels[parcels['ZONECLASS'].isin(['R-1', 'R-2', 'R-1A', 'R-2A', 'R-1H', 'R-2H', 'R-2AH']) & (parcels['Units'] > 0)]


In [10]:
print("For Middle Housing without the Hillside Overlay:")
print(f"Number of Non-Conforming Parcels: {(middle_housing_housings['legality'] == 0).sum()}")
print(f"Number of Non-Conforming Dwellings: {middle_housing_housings[middle_housing_housings['legality'] == 0]['Units'].sum()}")
percentage = (middle_housing_housings[middle_housing_housings['legality'] == 0]['Units'].sum() / middle_housing_housings['Units'].sum()) * 100
print(f"Share of Non-Conforming Dwellings (within the low-density flatlands only): {percentage:.2f}%")

print("\nFor Middle Housing with the Hillside Overlay:")
print(f"Number of Non-Conforming Parcels: {(middle_housing_housings_with_hillside['legality'] == 0).sum()}")
print(f"Number of Non-Conforming Dwellings: {middle_housing_housings_with_hillside[middle_housing_housings_with_hillside['legality'] == 0]['Units'].sum()}")
percentage = (middle_housing_housings_with_hillside[middle_housing_housings_with_hillside['legality'] == 0]['Units'].sum() / middle_housing_housings_with_hillside['Units'].sum()) * 100
print(f"Share of Non-Conforming Dwellings (including the hillside overlay): {percentage:.2f}%")

print("\n Legality ")

For Middle Housing without the Hillside Overlay:
Number of Non-Conforming Parcels: 3168
Number of Non-Conforming Dwellings: 23036.0
Share of Non-Conforming Dwellings (within the low-density flatlands only): 60.84%

For Middle Housing with the Hillside Overlay:
Number of Non-Conforming Parcels: 3813
Number of Non-Conforming Dwellings: 24798.0
Share of Non-Conforming Dwellings (including the hillside overlay): 53.61%

 Legality 


In [11]:
middle_housing_housings_with_hillside[(middle_housing_housings_with_hillside['legality'] == 0)].explore(tooltip=['SitusAddre', 'LotSize' , 'ZONECLASS', 'Units', 'legality'])